<a href="https://colab.research.google.com/github/joohoho/JaskierBulgarianPoet/blob/main/Jaskier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import numpy as np
import pandas as pd
# import matplotlib.pyplot as plt

In [3]:
import string
import re

import tensorflow as tf

from keras.utils import pad_sequences
from keras.models import Sequential
from keras.layers import Input, Embedding, Dense, LSTM, Dropout, Flatten

In [ ]:
# from transformers import LlamaForCausalLM, LlamaTokenizer, GenerationConfig
# tokenizer = LlamaTokenizer.from_pretrained("")
# model = LlamaForCausalLM.from_pretrained("")

Bulgarian Poems dataset are taken from [kaggle dataset](https://www.kaggle.com/datasets/auhide/bulgarian-poems).

In [4]:
poems_table = pd.read_csv("drive/MyDrive/chitanka-corpus.csv")

In [5]:
poems_table.head()

author                                   title  \
0      Андреас Неуман               (Гравитацията и грацията)   
1      Андреас Неуман                (Клаудия в библиотеката)   
2      Андреас Неуман                           (Лолита джаз)   
3  Александър Радонов                   (Моята) умираща мечта   
4        Хорхе Урутия  (Не поверителни) данни за една справка   

                                                poem  
0  Два съда с вода.<eol>Леко пързаляне с кънки.<e...  
1  Издирваш в книгите<eol>със странно усърдие на ...  
2  На Хусто Наваро и Хуан де Локса<eol>І<eol>Преч...  
3  Като рак ядяща,<eol>самотата подяжда<eol>нечия...  
4  че не пиша ръкописвам начертавам зачертавам по...

### Preprocessing

In [6]:
poems_table["poem"] = poems_table.poem.str.lower()

In [7]:
all_poems = poems_table.poem.values.tolist()

The stop words for Bulgarian language are taken from [Stopwords ISO](https://github.com/stopwords-iso/stopwords-bg).

In [8]:
with open("drive/MyDrive/stopwords-bg.txt", encoding="utf8") as f:
    text = f.read()

In [9]:
text

'а\nавтентичен\nаз\nако\nала\nбе\nбез\nбеше\nби\nбивш\nбивша\nбившо\nбил\nбила\nбили\nбило\nблагодаря\nблизо\nбъдат\nбъде\nбяха\nв\nвас\nваш\nваша\nвероятно\nвече\nвзема\nви\nвие\nвинаги\nвнимава\nвреме\nвсе\nвсеки\nвсички\nвсичко\nвсяка\nвъв\nвъпреки\nвърху\nг\nги\nглавен\nглавна\nглавно\nглас\nго\nгодина\nгодини\nгодишен\nд\nда\nдали\nдва\nдвама\nдвамата\nдве\nдвете\nден\nднес\nдни\nдо\nдобра\nдобре\nдобро\nдобър\nдокато\nдокога\nдори\nдосега\nдоста\nдруг\nдруга\nдруги\nе\nевтин\nедва\nедин\nедна\nеднаква\nеднакви\nеднакъв\nедно\nекип\nето\nживот\nза\nзабавям\nзад\nзаедно\nзаради\nзасега\nзаспал\nзатова\nзащо\nзащото\nи\nиз\nили\nим\nима\nимат\nиска\nй\nказа\nкак\nкаква\nкакво\nкакто\nкакъв\nкато\nкога\nкогато\nкоето\nкоито\nкой\nкойто\nколко\nкоято\nкъде\nкъдето\nкъм\nлесен\nлесно\nли\nлош\nм\nмай\nмалко\nме\nмежду\nмек\nмен\nмесец\nми\nмного\nмнозина\nмога\nмогат\nможе\nмокър\nмоля\nмомента\nму\nн\nна\nнад\nназад\nнай\nнаправи\nнапред\nнапример\nнас\nне\nнего\nнещо\nнея\nни\nние\nн

In [10]:
STOPWORDS = re.split("\W+", text)

In [12]:
NUM_TEXTS = max(poems_table.poem.index)
MIN_OCCURANCE = 10

In [ ]:
# Create a dictionary with preprocessed words

my_dict = []

def make_dict(data):
  for i in range(NUM_TEXTS):

    text = data[i].split()
    text = [word for word in text if word not in string.punctuation] # Removing punctuations
    text = [word for word in text if word.isalpha()] # removing all the words having characters other than letters

    text = [word for word in text if word not in STOPWORDS] #Removing all the stop words

    seq = ' '.join(text)
    split_seq = seq.split()

    for index in range(len(split_seq)):  # putting all the words in our corpus
      my_dict.append(split_seq[index])

  return my_dict

In [ ]:
my_dict = set(make_dict(all_poems))

In [ ]:
VOCAB_SIZE = len(my_dict)
VOCAB_SIZE

81153

Trqbva da namalq VOCAB siza, na GPT e 40 478.

In [ ]:
#Create vocabulary

vocab, index = {}, 1  # start indexing from 1
vocab['<pad>'] = 0  # add a padding token
for token in my_dict:
  if token not in vocab:
    vocab[token] = index
    index += 1
vocab_size = len(vocab)
print(vocab)

{'<pad>': 0, 'завъзлена': 1, 'предала': 2, 'двуполюсна': 3, 'несдържано': 4, 'изветряло': 5, 'попето': 6, 'народа': 7, 'сливници': 8, 'ценните': 9, 'меко': 10, 'отронена': 11, 'техническа': 12, 'загрубя': 13, 'понася': 14, 'мечтах': 15, 'врабчетата': 16, 'дантеленият': 17, 'пилотите': 18, 'жертвеници': 19, 'буднооко': 20, 'фантазирах': 21, 'смеси': 22, 'хладни': 23, 'изчакали': 24, 'рединготите': 25, 'веществата': 26, 'юлио': 27, 'гробна': 28, 'издигали': 29, 'поданството': 30, 'разстройвам': 31, 'трепетликата': 32, 'издигащия': 33, 'кон': 34, 'цепя': 35, 'скочи': 36, 'измъквай': 37, 'безсъницата': 38, 'пятна': 39, 'заровения': 40, 'пльосва': 41, 'везана': 42, 'виниловата': 43, 'левия': 44, 'разпределя': 45, 'порязана': 46, 'безделници': 47, 'твърдокаменен': 48, 'концертните': 49, 'каси': 50, 'изгладя': 51, 'фуриозото': 52, 'иаший': 53, 'франклин': 54, 'очарована': 55, 'бик': 56, 'авксеитиева': 57, 'бензинов': 58, 'къщни': 59, 'изхожда': 60, 'celeste': 61, 'незвучният': 62, 'извисява':

In [ ]:
vocab["дръзнах"]

65116

In [ ]:
# Create an inverse vocabulary

inverse_vocab = {index: token for token, index in vocab.items()}
print(inverse_vocab)

{0: '<pad>', 1: 'завъзлена', 2: 'предала', 3: 'двуполюсна', 4: 'несдържано', 5: 'изветряло', 6: 'попето', 7: 'народа', 8: 'сливници', 9: 'ценните', 10: 'меко', 11: 'отронена', 12: 'техническа', 13: 'загрубя', 14: 'понася', 15: 'мечтах', 16: 'врабчетата', 17: 'дантеленият', 18: 'пилотите', 19: 'жертвеници', 20: 'буднооко', 21: 'фантазирах', 22: 'смеси', 23: 'хладни', 24: 'изчакали', 25: 'рединготите', 26: 'веществата', 27: 'юлио', 28: 'гробна', 29: 'издигали', 30: 'поданството', 31: 'разстройвам', 32: 'трепетликата', 33: 'издигащия', 34: 'кон', 35: 'цепя', 36: 'скочи', 37: 'измъквай', 38: 'безсъницата', 39: 'пятна', 40: 'заровения', 41: 'пльосва', 42: 'везана', 43: 'виниловата', 44: 'левия', 45: 'разпределя', 46: 'порязана', 47: 'безделници', 48: 'твърдокаменен', 49: 'концертните', 50: 'каси', 51: 'изгладя', 52: 'фуриозото', 53: 'иаший', 54: 'франклин', 55: 'очарована', 56: 'бик', 57: 'авксеитиева', 58: 'бензинов', 59: 'къщни', 60: 'изхожда', 61: 'celeste', 62: 'незвучният', 63: 'извися

In [ ]:
inverse_vocab[9]

'ценните'

We would be preprocessing our poems again keeping only words that are present in our dictionary list.

In [ ]:
def clean_data(data, vocab = vocab):
  # for i in range(NUM_TEXTS):
  text = data.split()
  text = [word for word in text if word not in string.punctuation] # Removing punctuations
  text = [word for word in text if word.isalpha()] # removing all the words having characters other than letters
  text = [word for word in text if word not in STOPWORDS] #Removing all the stop words
  text = [word for word in text if word in my_dict]
  seq = ' '.join(text)

  seq = seq.split()
  number_list = [vocab[word] for word in seq]

  return number_list

In [ ]:
clean_data(poems_table.poem[0]), clean_data(poems_table.poem[1])

In [ ]:
corpus = []
for i in range(NUM_TEXTS):
    clean_text = clean_data(poems_table.poem[i]) # cleaning up the poem
    corpus.append(clean_text) # adding the preprocessed poem to our list

In [ ]:
corpus[0]

[80667,
 78518,
 50482,
 36639,
 79705,
 14751,
 34707,
 20305,
 23098,
 58065,
 51549,
 31588,
 27594]

The next step is to encode each word as a sequence of integers. Tokenizer lass in the Keras API can be used to encode the words as a sequence of integers. We train the tokenizer on all the poems in our dataset and it develops a vocabulary of all the tokens in the dataset and uses these tokens to create a consistent mapping from tokens in the vocabulary to unique integers.

One of the biggest problems with text is that it is messy and unstructured, and machine learning algorithms prefer structured, well defined fixed-length inputs and by using the Bag-of-Words technique we can convert variable-length texts into a fixed-length vector. Also, at a much granular level, the machine learning models work with numerical data rather than textual data. So to be more specific, by using the bag-of-words (BoW) technique, we convert a text into its equivalent vector of numbers.
Let's now vectorize our words.

In [ ]:
type(corpus[0])

list

In [ ]:
SEQUENCE_LENGTH = 700

In [ ]:
x_padded = tf.keras.utils.pad_sequences(corpus, maxlen = SEQUENCE_LENGTH, padding = "post")

In [ ]:
type(x_padded)

numpy.ndarray

The longest sequence is above 4000, so I will reduce the length of each sequence manually to 1000.

### Modelyt po dolu e za predskazvane na sledvasht token

Ako imam vreme moje da se napravi sequences na parcheta sys sliding window,koito da se prepokrivat s tf.data.Dataset; stava s skip() i take()

In [ ]:
BATCH_SIZE = 32

In [ ]:
tf.keras.backend.clear_session()

In [ ]:
model = Sequential([
    Embedding(input_dim = VOCAB_SIZE, output_dim = 128, input_length = SEQUENCE_LENGTH),
    # Embedding(input_dim = 128, output_dim = 64),
    LSTM(8, return_sequences = True, activation = "tanh"),
    LSTM(16, return_sequences = True, activation = "tanh"),
    LSTM(8, activation = "tanh", return_sequences = True),

    Dense(VOCAB_SIZE, activation = "softmax")
])

In [ ]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 700, 128)          10387584  
                                                                 
 lstm (LSTM)                 (None, 700, 8)            4384      
                                                                 
 lstm_1 (LSTM)               (None, 700, 16)           1600      
                                                                 
 lstm_2 (LSTM)               (None, 700, 8)            800       
                                                                 
 dense (Dense)               (None, 700, 81153)        730377    
                                                                 
Total params: 11124745 (42.44 MB)
Trainable params: 11124745 (42.44 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [ ]:
model.compile(loss = "sparse_categorical_crossentropy")

In [ ]:
model.fit(x_padded[:10], x_padded[1:11])

1/1 [==============================] - 17s 17s/step - loss: 11.3039


In [ ]:
predictions = model.predict(x_padded[:10])

1/1 [==============================] - 6s 6s/step


We receive for every vector another vector with probabilities.

In [ ]:
tf.argmax(predictions, axis = 1)

<tf.Tensor: shape=(10,), dtype=int64, numpy=array([9203, 9203, 9203, 9203, 9203, 9203, 9203, 9203, 9203, 9203])>